In [3]:
import pandas
from typing import Tuple, List
from sqlalchemy.orm import relationship
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy import Column, Integer, String, Boolean, ForeignKey
from sqlalchemy import func
from typing import List
from sqlalchemy import create_engine
from sqlalchemy.orm import sessionmaker

Base = declarative_base()

class Config:
    def __init__(self):
        self.DB_NAME = "test-1.db"

class Country(Base):
    __tablename__ = 'country'

    country_id = Column(Integer, primary_key=True)
    name = Column(String(100), nullable=False)
    first_letter = Column(String(1), nullable=False)
    last_letter = Column(String(1), nullable=False)

    states = relationship('State', back_populates='country')

    def __repr__(self) -> str:
        return f"Country(country_id={self.country_id!r}, name={self.name!r})"

class State(Base):
    __tablename__ = 'state'

    state_id = Column(Integer, primary_key=True)
    name = Column(String(100), nullable=False)
    country_id = Column(Integer, ForeignKey('country.country_id'), nullable=False)
    first_letter = Column(String(1), nullable=False)
    last_letter = Column(String(1), nullable=False)
    is_capital_state = Column(Boolean, nullable=False, default=False)

    country = relationship('Country', back_populates='states')
    cities = relationship('City', back_populates='state')

    def __repr__(self) -> str:
        return f"State(state_id={self.state_id!r}, name={self.name!r})"

class City(Base):
    __tablename__ = 'city'

    city_id = Column(Integer, primary_key=True)
    name = Column(String(100), nullable=False)
    state_id = Column(Integer, ForeignKey('state.state_id'), nullable=False)
    country_id = Column(Integer, ForeignKey('country.country_id'), nullable=False)

    state = relationship('State', back_populates='cities')
    country = relationship('Country')

    def __repr__(self) -> str:
        return f"City(city_id={self.city_id!r}, name={self.name!r})"

class DBConnector:
    def __init__(self, db_name):
        self.db_name = db_name
        self.engine = create_engine(f"sqlite:///{db_name}")
        Base.metadata.create_all(self.engine)
        Session = sessionmaker(bind=self.engine)
        self.session = Session()

    def close_connection(self):
        self.session.close()

class DBOperations:
    def __init__(self):
        self.config = Config()
        self.db_connector = DBConnector(self.config.DB_NAME)

    def insert_country(self, name, first_letter, last_letter):
        country = Country(name=name, first_letter=first_letter, last_letter=last_letter)
        self.db_connector.session.add(country)
        self.db_connector.session.commit()
        print(f"Added country: {country}")

    def insert_state(self, name, country_id, first_letter, last_letter, is_capital_state=False):
        state = State(name=name, country_id=country_id, first_letter=first_letter,
                        last_letter=last_letter, is_capital_state=is_capital_state)
        self.db_connector.session.add(state)
        self.db_connector.session.commit()
        print(f"Added state: {state}")

    def insert_city(self, name, state_id, country_id):
        city = City(name=name, state_id=state_id, country_id=country_id)
        self.db_connector.session.add(city)
        self.db_connector.session.commit()
        print(f"Added city: {city}")

    def insert_countries_bulk(self, countries_data: List[tuple]):
        countries = [Country(name=name, first_letter=first_letter, last_letter=last_letter) for name, first_letter, last_letter in countries_data]
        self.db_connector.session.add_all(countries)
        self.db_connector.session.commit()
        print("Added countries in bulk.")

    def insert_states_bulk(self, states_data: List[tuple]):
        states = [State(name=name, country_id=country_id, first_letter=first_letter, last_letter=last_letter, is_capital_state=is_capital_state) for name, country_id, first_letter, last_letter, is_capital_state in states_data]
        self.db_connector.session.add_all(states)
        self.db_connector.session.commit()
        print("Added states in bulk.")

    def insert_cities_bulk(self, cities_data: List[tuple]):
        cities = [City(name=name, state_id=state_id, country_id=country_id) for name, state_id, country_id in cities_data]
        self.db_connector.session.add_all(cities)
        self.db_connector.session.commit()
        print("Added cities in bulk.")

    def get_all_countries(self):
        return self.db_connector.session.query(Country).all()

    def get_all_states(self):
        return self.db_connector.session.query(State).all()

    def get_all_cities(self):
        return self.db_connector.session.query(City).all()

    def countries_with_identical_first_and_last_letters(self):
        return self.db_connector.session.query(Country.name).filter(Country.first_letter == Country.last_letter).all()

    def states_with_identical_first_and_last_letters(self):
        return self.db_connector.session.query(Country.name, State.name).\
            join(State, State.country_id == Country.country_id).\
            filter(State.first_letter == State.last_letter).all()

    def cities_with_prime_length_names(self):
        return self.db_connector.session.query(City.name, Country.name).\
            join(Country, City.country_id == Country.country_id).\
            filter(func.LENGTH(City.name).in_([2, 3, 5, 7, 11, 13, 17, 19, 23, 29, 31, 37, 41, 43, 47, 53, 59, 61, 67, 71, 73, 79, 83, 89, 97])).all()

class DataExtractor:
    def __init__(self, countries_csv_path, states_csv_path, cities_csv_path):
        self.countries_df = pandas.read_csv(countries_csv_path)
        self.states_df = pandas.read_csv(states_csv_path)
        self.cities_df = pandas.read_csv(cities_csv_path)

    def get_df(self):
        return self.countries_df, self.states_df, self.cities_df

class DataTransformer:
    def __init__(self, countries_df, states_df, cities_df):
        self.countries_df = countries_df
        self.states_df = states_df
        self.cities_df = cities_df
        self.transformed_countries = self._transform_countries()
        self.transformed_states = self._transform_states()
        self.transformed_cities = self._transform_cities()

    def _transform_countries(self):
        countries = []
        for _, row in self.countries_df.iterrows():
            country = Country(
                country_id=row['id'],
                name=row['name'],
                first_letter=row['name'][0].lower(),
                last_letter=row['name'][-1].lower()
            )
            countries.append(country)
        return countries

    def _transform_states(self):
        states = []
        for _, row in self.states_df.iterrows():
            state = State(
                state_id=row['id'],
                name=row['name'],
                country_id=row['country_id'],
                first_letter=row['name'][0].lower(),
                last_letter=row['name'][-1].lower(),
                is_capital_state=self._check_is_capital_state(row['country_id'], row['name'])
            )
            states.append(state)
        return states
    
    def _check_is_capital_state(self, country_id, state_name) -> bool:
        country_capital = self.countries_df.loc[self.countries_df['id'] == country_id, 'capital'].iloc[0]
        
        if isinstance(country_capital, str) and isinstance(state_name, str):
            # Check if state_name is a substring of country_capital or vice versa
            if state_name in country_capital or country_capital in state_name:
                return True
        
        return False

    def _transform_cities(self):
        cities = []
        for _, row in self.cities_df.iterrows():
            if isinstance(row['name'], str):
                city_name = row['name']
            else:
                city_name = "Unknown City"
            city = City(
                city_id=row['id'],
                name=city_name,
                state_id=row['state_id'],
                country_id=row['country_id']
            )
            cities.append(city)
        return cities
    
    def get_transformed_data(self) -> Tuple[List[Country], List[State], List[City]]:
        return self.transformed_countries, self.transformed_states, self.transformed_cities

class DataLoader:
    def __init__(self, db_operations: DBOperations):
        self.db_operations = db_operations

    def load_transformed_countries(self, transformed_countries: List[Country]):
        countries_data = [(country.name, country.first_letter, country.last_letter) for country in transformed_countries]
        self.db_operations.insert_countries_bulk(countries_data)

    def load_transformed_states(self, transformed_states: List[State]):
        states_data = [(state.name, state.country_id, state.first_letter, state.last_letter, state.is_capital_state) for state in transformed_states]
        self.db_operations.insert_states_bulk(states_data)

    def load_transformed_cities(self, transformed_cities: List[City]):
        cities_data = [(city.name, city.state_id, city.country_id) for city in transformed_cities]
        self.db_operations.insert_cities_bulk(cities_data)

class EtlDriver:
    def __init__(self, countries_csv_path, states_csv_path, cities_csv_path):
        self.db_operations = DBOperations()
        self.extractor = DataExtractor(countries_csv_path, states_csv_path, cities_csv_path)
        self.countries_df, self.states_df, self.cities_df = self.extractor.get_df()
        self.transformer = DataTransformer(self.countries_df, self.states_df, self.cities_df)
        self.transformed_countries, self.transformed_states, self.transformed_cities = self.transformer.get_transformed_data()
        self.data_loader = DataLoader(self.db_operations)

    def run_etl_process(self):
        self.data_loader.load_transformed_countries(self.transformed_countries)
        self.data_loader.load_transformed_states(self.transformed_states)
        self.data_loader.load_transformed_cities(self.transformed_cities)

C:\Users\adimi\AppData\Local\Temp\ipykernel_26724\2233513806.py:11: MovedIn20Warning: The ``declarative_base()`` function is now available as sqlalchemy.orm.declarative_base(). (deprecated since: 2.0) (Background on SQLAlchemy 2.0 at: https://sqlalche.me/e/b8d9)
  Base = declarative_base()


In [4]:
etl_driver = EtlDriver(
    countries_csv_path=r"C:\Users\adimi\Documents\Adimis\Assignments\Vodafone\src\data\countries.csv",
    states_csv_path=r"C:\Users\adimi\Documents\Adimis\Assignments\Vodafone\src\data\states.csv",
    cities_csv_path=r"C:\Users\adimi\Documents\Adimis\Assignments\Vodafone\src\data\cities.csv"
)
etl_driver.run_etl_process()

Added countries in bulk.
Added states in bulk.
Added cities in bulk.


In [5]:
db_connector = DBConnector("loader-test.db")
db_operations = DBOperations(db_connector)
print(db_operations.get_all_countries())

[Country(country_id=1, name='Afghanistan'), Country(country_id=2, name='Aland Islands'), Country(country_id=3, name='Albania'), Country(country_id=4, name='Algeria'), Country(country_id=5, name='American Samoa'), Country(country_id=6, name='Andorra'), Country(country_id=7, name='Angola'), Country(country_id=8, name='Anguilla'), Country(country_id=9, name='Antarctica'), Country(country_id=10, name='Antigua And Barbuda'), Country(country_id=11, name='Argentina'), Country(country_id=12, name='Armenia'), Country(country_id=13, name='Aruba'), Country(country_id=14, name='Australia'), Country(country_id=15, name='Austria'), Country(country_id=16, name='Azerbaijan'), Country(country_id=17, name='Bahrain'), Country(country_id=18, name='Bangladesh'), Country(country_id=19, name='Barbados'), Country(country_id=20, name='Belarus'), Country(country_id=21, name='Belgium'), Country(country_id=22, name='Belize'), Country(country_id=23, name='Benin'), Country(country_id=24, name='Bermuda'), Country(co

In [6]:
print(db_operations.get_all_states())

[State(state_id=1, name='Badakhshan'), State(state_id=2, name='Badghis'), State(state_id=3, name='Baghlan'), State(state_id=4, name='Balkh'), State(state_id=5, name='Bamyan'), State(state_id=6, name='Daykundi'), State(state_id=7, name='Farah'), State(state_id=8, name='Faryab'), State(state_id=9, name='Ghazni'), State(state_id=10, name='Ghōr'), State(state_id=11, name='Helmand'), State(state_id=12, name='Herat'), State(state_id=13, name='Jowzjan'), State(state_id=14, name='Kabul'), State(state_id=15, name='Kandahar'), State(state_id=16, name='Kapisa'), State(state_id=17, name='Khost'), State(state_id=18, name='Kunar'), State(state_id=19, name='Kunduz Province'), State(state_id=20, name='Laghman'), State(state_id=21, name='Logar'), State(state_id=22, name='Nangarhar'), State(state_id=23, name='Nimruz'), State(state_id=24, name='Nuristan'), State(state_id=25, name='Paktia'), State(state_id=26, name='Paktika'), State(state_id=27, name='Panjshir'), State(state_id=28, name='Parwan'), State(s

In [7]:
print(db_operations.get_all_cities())

[City(city_id=1, name='Ashkāsham'), City(city_id=2, name='Fayzabad'), City(city_id=3, name='Jurm'), City(city_id=4, name='Khandūd'), City(city_id=5, name='Rāghistān'), City(city_id=6, name='Wākhān'), City(city_id=7, name='Ghormach'), City(city_id=8, name='Qala i Naw'), City(city_id=9, name='Baghlān'), City(city_id=10, name='Ḩukūmatī Dahanah-ye Ghōrī'), City(city_id=11, name='Nahrīn'), City(city_id=12, name='Pul-e Khumrī'), City(city_id=13, name='Balkh'), City(city_id=14, name='Dowlatābād'), City(city_id=15, name='Khulm'), City(city_id=16, name='Lab-Sar'), City(city_id=17, name='Mazār-e Sharīf'), City(city_id=18, name='Qarchī Gak'), City(city_id=19, name='Bāmyān'), City(city_id=20, name='Panjāb'), City(city_id=21, name='Nīlī'), City(city_id=22, name='Farah'), City(city_id=23, name='Andkhoy'), City(city_id=24, name='Maymana'), City(city_id=25, name='Ghazni'), City(city_id=26, name='Fayrōz Kōh'), City(city_id=27, name='Shahrak'), City(city_id=28, name='‘Alāqahdārī Dīshū'), City(city_id=29